In [ ]:
%tensorflow_version 1.x

TensorFlow 1.x selected.


In [ ]:
import pandas as pd
import numpy as np
import tensorflow as tf
import os
from os import listdir
from os.path import isfile, join
from collections import namedtuple
from tensorflow.python.layers.core import Dense
from tensorflow.python.ops.rnn_cell_impl import _zero_state_tensors
import time
import re
from sklearn.model_selection import train_test_split
from tqdm import tqdm_notebook
from math import ceil
from nltk.tokenize import word_tokenize
import json

In [ ]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

# Building the Model

In [ ]:
def model_inputs():
    '''Create palceholders for inputs to the model'''
    
    with tf.name_scope('inputs'):
        inputs = tf.placeholder(tf.int32, [None, None], name='inputs')
    with tf.name_scope('targets'):
        targets = tf.placeholder(tf.int32, [None, None], name='targets')
    keep_prob = tf.placeholder(tf.float32, name='keep_prob')
    inputs_length = tf.placeholder(tf.int32, (None,), name='inputs_length')
    targets_length = tf.placeholder(tf.int32, (None,), name='targets_length')

    # Computes the maximum of elements across dimensions of a tensor.
    max_target_length = tf.reduce_max(targets_length, name='max_target_len')

    return inputs, targets, keep_prob, inputs_length, targets_length, max_target_length

In [ ]:
def process_encoding_input(targets, vocab_to_int, batch_size):
    '''Remove the last word id from each batch and concat the <GO> to the begining of each batch'''
    
    with tf.name_scope("process_encoding"):
        ending = tf.strided_slice(targets, [0, 0], [batch_size, -1], [1, 1])
        dec_input = tf.concat([tf.fill([batch_size, 1], vocab_to_int['<GO>']), ending], 1)

    return dec_input

In [ ]:
def encoding_layer(rnn_size, sequence_length, num_layers, rnn_inputs, keep_prob, direction):
    '''Create the encoding layer'''
    
    if direction == 1:
        # For 1D cell
        with tf.name_scope("RNN_Encoder_Cell_1D"):
            for layer in range(num_layers):
                with tf.variable_scope('encoder_{}'.format(layer)):
                    # Long short-term memory unit (LSTM) recurrent network cell.
                    lstm = tf.contrib.rnn.LSTMCell(rnn_size)

                    # Operator adding dropout to inputs and outputs of the given cell.
                    drop = tf.contrib.rnn.DropoutWrapper(lstm, 
                                                         input_keep_prob = keep_prob)

                    # Creates a recurrent neural network specified by RNNCell cell
                    enc_output, enc_state = tf.nn.dynamic_rnn(drop, 
                                                              rnn_inputs,
                                                              sequence_length,
                                                              dtype=tf.float32)

            return enc_output, enc_state
        
        
    if direction == 2:
        # For 2D cell
        with tf.name_scope("RNN_Encoder_Cell_2D"):
            for layer in range(num_layers):
                with tf.variable_scope('encoder_{}'.format(layer)):
                    # For the first direction
                    cell_fw = tf.contrib.rnn.LSTMCell(rnn_size)
                    cell_fw = tf.contrib.rnn.DropoutWrapper(cell_fw, 
                                                            input_keep_prob = keep_prob)

                    # For the second direction
                    cell_bw = tf.contrib.rnn.LSTMCell(rnn_size)
                    cell_bw = tf.contrib.rnn.DropoutWrapper(cell_bw, 
                                                            input_keep_prob = keep_prob)

                    # Creates a dynamic version of bidirectional recurrent neural network
                    enc_output, enc_state = tf.nn.bidirectional_dynamic_rnn(cell_fw, 
                                                                            cell_bw, 
                                                                            rnn_inputs,
                                                                            sequence_length,
                                                                            dtype=tf.float32)
            # Join outputs since we are using a bidirectional RNN
            enc_output = tf.concat(enc_output,2)
            # Use only the forward state because the model can't use both states at once
            return enc_output, enc_state[0]

In [ ]:
def training_decoding_layer(dec_embed_input, targets_length, dec_cell, initial_state, output_layer, 
                            vocab_size, max_target_length):
    '''Create the training logits'''

    with tf.name_scope("Training_Decoder"):
        training_helper = tf.contrib.seq2seq.TrainingHelper(inputs=dec_embed_input,
                                                            sequence_length=targets_length,
                                                            time_major=False)

        training_decoder = tf.contrib.seq2seq.BasicDecoder(dec_cell,
                                                           training_helper,
                                                           initial_state,
                                                           output_layer) 

        training_logits, _ ,_ = tf.contrib.seq2seq.dynamic_decode(training_decoder,
                                                                  output_time_major=False,
                                                                  impute_finished=True,
                                                                  maximum_iterations=max_target_length)
        return training_logits

In [ ]:
def inference_decoding_layer(embeddings, start_token, end_token, dec_cell, initial_state, output_layer,
                             max_target_length, batch_size):
    '''Create the inference logits'''

    with tf.name_scope("Inference_Decoder"):
        # Constructs a tensor by tiling a given tensor.
        start_tokens = tf.tile(tf.constant([start_token], dtype=tf.int32), [batch_size], name='start_tokens')

        inference_helper = tf.contrib.seq2seq.GreedyEmbeddingHelper(embeddings,
                                                                    start_tokens,
                                                                    end_token)

        inference_decoder = tf.contrib.seq2seq.BasicDecoder(dec_cell,
                                                            inference_helper,
                                                            initial_state,
                                                            output_layer)

        inference_logits, _ ,_ = tf.contrib.seq2seq.dynamic_decode(inference_decoder,
                                                                  output_time_major=False,
                                                                  impute_finished=True,
                                                                  maximum_iterations=max_target_length)

        return inference_logits

In [ ]:
def decoding_layer(dec_embed_input, embeddings, enc_output, enc_state, vocab_size, inputs_length, targets_length, 
                   max_target_length, rnn_size, vocab_to_int, keep_prob, batch_size, num_layers, direction):
    '''Create the decoding cell and attention for the training and inference decoding layers'''
    
    with tf.name_scope("RNN_Decoder_Cell"):
        for layer in range(num_layers):
            with tf.variable_scope('decoder_{}'.format(layer)):
                lstm = tf.contrib.rnn.LSTMCell(rnn_size)
                dec_cell = tf.contrib.rnn.DropoutWrapper(lstm, 
                                                         input_keep_prob = keep_prob)
    
    output_layer = Dense(vocab_size,
                         kernel_initializer = tf.truncated_normal_initializer(mean = 0.0, stddev=0.1))

    attn_mech = tf.contrib.seq2seq.BahdanauAttention(rnn_size,
                                                  enc_output,
                                                  inputs_length,
                                                  normalize=False,
                                                  name='BahdanauAttention')
  
    # Wraps another RNNCell with attention.
    with tf.name_scope("Attention_Wrapper"):
        dec_cell = tf.contrib.seq2seq.AttentionWrapper(dec_cell,
                                                              attn_mech,
                                                              rnn_size)
    
    initial_state = dec_cell.zero_state(batch_size=batch_size,dtype=tf.float32).clone(cell_state=enc_state)

    with tf.variable_scope("decode"):
        training_logits = training_decoding_layer(dec_embed_input, 
                                                  targets_length, 
                                                  dec_cell, 
                                                  initial_state,
                                                  output_layer,
                                                  vocab_size, 
                                                  max_target_length)
    with tf.variable_scope("decode", reuse=True):
        inference_logits = inference_decoding_layer(embeddings,  
                                                    vocab_to_int['<GO>'], 
                                                    vocab_to_int['<EOS>'],
                                                    dec_cell, 
                                                    initial_state, 
                                                    output_layer,
                                                    max_target_length,
                                                    batch_size)

    return training_logits, inference_logits

In [ ]:
def seq2seq_model(inputs, targets, keep_prob, inputs_length, targets_length, max_target_length, 
                  vocab_size, rnn_size, num_layers, vocab_to_int, batch_size, embedding_size, direction):
    '''Use the previous functions to create the training and inference logits'''
    
    enc_embeddings = tf.Variable(tf.random_uniform([vocab_size, embedding_size], -1, 1))
    enc_embed_input = tf.nn.embedding_lookup(enc_embeddings, inputs)
    enc_output, enc_state = encoding_layer(rnn_size, inputs_length, num_layers, 
                                           enc_embed_input, keep_prob, direction)

    dec_embeddings = tf.Variable(tf.random_uniform([vocab_size, embedding_size], -1, 1))
    dec_input = process_encoding_input(targets, vocab_to_int, batch_size)
    dec_embed_input = tf.nn.embedding_lookup(dec_embeddings, dec_input)
    
    training_logits, inference_logits  = decoding_layer(dec_embed_input, 
                                                        dec_embeddings,
                                                        enc_output,
                                                        enc_state, 
                                                        vocab_size, 
                                                        inputs_length, 
                                                        targets_length, 
                                                        max_target_length,
                                                        rnn_size, 
                                                        vocab_to_int, 
                                                        keep_prob, 
                                                        batch_size,
                                                        num_layers,
                                                        direction)
    
    return training_logits, inference_logits

In [ ]:
def pad_sentence_batch(sentence_batch):
    """Pad sentences with <PAD> so that each sentence of a batch has the same length"""
    max_sentence = max([len(sentence) for sentence in sentence_batch])
    return [sentence + [vocab_to_int['<PAD>']] * (max_sentence - len(sentence)) for sentence in sentence_batch]

In [ ]:
def get_batches(sentences, batch_size, threshold):
    """Batch sentences, noisy sentences, and the lengths of their sentences together.
       With each epoch, sentences will receive new mistakes"""
    
    for batch_i in range(0, len(sentences)//batch_size):
        start_i = batch_i * batch_size
        sentences_batch = sentences[start_i:start_i + batch_size]
        
        # Noisy sentences generation
        sentences_batch_noisy = []
        for sentence in sentences_batch:
            sentences_batch_noisy.append(noise_maker(sentence, threshold))

        # Batch sentences with EOS tag
        sentences_batch_eos = []
        for sentence in sentences_batch:
            sentence.append(vocab_to_int['<EOS>'])
            sentences_batch_eos.append(sentence)

        pad_sentences_batch = np.array(pad_sentence_batch(sentences_batch_eos))
        pad_sentences_noisy_batch = np.array(pad_sentence_batch(sentences_batch_noisy))
        
        # Need the lengths for the _lengths parameters
        pad_sentences_lengths = []
        for sentence in pad_sentences_batch:
            pad_sentences_lengths.append(len(sentence))
        
        pad_sentences_noisy_lengths = []
        for sentence in pad_sentences_noisy_batch:
            pad_sentences_noisy_lengths.append(len(sentence))
        
        yield pad_sentences_noisy_batch, pad_sentences_batch, pad_sentences_noisy_lengths, pad_sentences_lengths

*Note: This set of values achieved the best results.*

In [ ]:
# The default parameters
epochs = 100
batch_size = 64
num_layers = 2
rnn_size = 512
embedding_size = 128
learning_rate = 0.0005
direction = 2
threshold = 0.95
keep_probability = 0.75

In [ ]:
def build_graph(keep_prob, rnn_size, num_layers, batch_size, learning_rate, embedding_size, direction, vocab_to_int):

    tf.compat.v1.reset_default_graph()
    
    # Load the model inputs    
    inputs, targets, keep_prob, inputs_length, targets_length, max_target_length = model_inputs()

    # Create the training and inference logits
    training_logits, inference_logits = seq2seq_model(tf.reverse(inputs, [-1]),
                                                      targets, 
                                                      keep_prob,   
                                                      inputs_length,
                                                      targets_length,
                                                      max_target_length,
                                                      len(vocab_to_int)+1,
                                                      rnn_size, 
                                                      num_layers, 
                                                      vocab_to_int,
                                                      batch_size,
                                                      embedding_size,
                                                      direction)

    # Create tensors for the training logits and inference logits
    training_logits = tf.identity(training_logits.rnn_output, 'logits')

    with tf.name_scope('predictions'):
        predictions = tf.identity(inference_logits.sample_id, name='predictions')
        tf.summary.histogram('predictions', predictions)

    # Create the weights for sequence_loss
    masks = tf.sequence_mask(targets_length, max_target_length, dtype=tf.float32, name='masks')
    
    with tf.name_scope("cost"):
        # Loss function
        cost = tf.contrib.seq2seq.sequence_loss(training_logits, 
                                                targets, 
                                                masks)
        tf.summary.scalar('cost', cost)
    
    # with tf.name_scope("test_cost"):
    #     # Loss function
    #     test_cost = tf.contrib.seq2seq.sequence_loss(tf.identity(inference_logits.rnn_output, 'infer_logits'), 
    #                                             targets, 
    #                                             masks)
    #     tf.summary.scalar('test_cost', test_cost)

    with tf.name_scope("optimze"):
        optimizer = tf.train.AdamOptimizer(learning_rate)

        # Gradient Clipping
        gradients = optimizer.compute_gradients(cost)
        capped_gradients = [(tf.clip_by_value(grad, -5., 5.), var) for grad, var in gradients if grad is not None]
        train_op = optimizer.apply_gradients(capped_gradients)

    # Merge all of the summaries
    merged = tf.summary.merge_all()    

    # Export the nodes 
    export_nodes = ['inputs', 'targets', 'keep_prob', 'cost', 'inputs_length', 'targets_length',
                    'predictions', 'merged', 'train_op','optimizer']
    Graph = namedtuple('Graph', export_nodes)
    local_dict = locals()
    graph = Graph(*[local_dict[each] for each in export_nodes])

    return graph

# Работаем с данными


In [ ]:
from google.colab import drive

In [ ]:
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
os.listdir()

['.config', 'drive', 'sample_data']

In [ ]:
import os
os.chdir('drive/My Drive/FunnyHeadlineProject')

In [ ]:
import pandas as pd

oneliners = pd.read_csv("MinEditedHeadlines.csv", index_col='Unnamed: 0')

In [ ]:
oneliners.head()

fun  ...   source
0  partially faded hand stamp undermining everyth...  ...  unfunme
1  partially faded hand stamp undermining everyth...  ...  unfunme
2  synthesizer trumpet announces arrival of porn ...  ...  unfunme
3  synthesizer trumpet announces arrival of porn ...  ...  unfunme
4  depressed security guard turns big flashlight ...  ...  unfunme

[5 rows x 3 columns]

In [ ]:
oneliners.values[:12]

array([['partially faded hand stamp undermining everything prosecutor says',
        'partially faded hand print undermining everything prosecutor claims',
        'unfunme'],
       ['partially faded hand stamp undermining everything prosecutor says',
        'partially faded hand stamp undermines prosecutor', 'unfunme'],
       ['synthesizer trumpet announces arrival of porn king',
        'electronic music for porn soundtrack', 'unfunme'],
       ['synthesizer trumpet announces arrival of porn king',
        'synthesizer trumpet announces arrival of pop king', 'unfunme'],
       ['depressed security guard turns big flashlight on self',
        'selfie light shows deep depression', 'unfunme'],
       ['depressed security guard turns big flashlight on self',
        'depressed security guard turns gun on self', 'unfunme'],
       ['depressed security guard turns big flashlight on self',
        'security guard turns big flashlight on self', 'unfunme'],
       ['fugitive doctor accuses

In [ ]:
pairs = oneliners[['serious','fun']].values

In [ ]:
pairs[:5]

array([['partially faded hand print undermining everything prosecutor claims',
        'partially faded hand stamp undermining everything prosecutor says'],
       ['partially faded hand stamp undermines prosecutor',
        'partially faded hand stamp undermining everything prosecutor says'],
       ['electronic music for porn soundtrack',
        'synthesizer trumpet announces arrival of porn king'],
       ['synthesizer trumpet announces arrival of pop king',
        'synthesizer trumpet announces arrival of porn king'],
       ['selfie light shows deep depression',
        'depressed security guard turns big flashlight on self']],
      dtype=object)

In [ ]:
len(pairs)

3785

In [ ]:
pairs = (tuple(i) for i in pairs)

In [ ]:
pairs = [(word_tokenize(a),word_tokenize(b)) for a,b in pairs]

In [ ]:
int_to_vocab = []

# Generating int -> vocabulary map (using list indexing)
for pair in pairs:
  for char in pair[0]+pair[1]:
    if char not in int_to_vocab:
      int_to_vocab.append(char)

int_to_vocab += ['<GO>','<PAD>','<EOS>']
vocab_to_int = {val:key for key,val in enumerate(int_to_vocab)}

In [ ]:
len(int_to_vocab)

9441

In [ ]:
id_pairs = [([vocab_to_int[i] for i in erroneous], [vocab_to_int[j] for j in true]) for erroneous, true in pairs]

In [ ]:
print(id_pairs[0][0])

[0, 1, 2, 3, 4, 5, 6, 7]


In [ ]:
print(id_pairs[0][0])

[0, 1, 2, 3, 4, 5, 6, 7]


In [ ]:
print(id_pairs[1][0])

[0, 1, 2, 8, 10, 6]


In [ ]:
training, testing = train_test_split(id_pairs, test_size = 0.2, random_state = 42)
training, validation = train_test_split(training, test_size = 0.05, random_state = 42)

In [ ]:
training = sorted(training, key=lambda x: len(x[1]))
validation = sorted(validation, key=lambda x: len(x[0]))
testing = sorted(testing, key=lambda x: len(x[0]))

In [ ]:
print(testing[0][0])

[2127]


In [ ]:
print(testing[1][0])

[1602]


In [ ]:
len(testing)

757

Параметры изначально мы взяли оригинальные, а потом в процессе обучения уменьшали их, благодаря этому лосс стал уменьшаться быстрее и стабильнее

In [ ]:
epochs = 100
batch_size = 128 #64
num_layers = 2
rnn_size = 256 #512
embedding_size = 128
learning_rate = 0.0005
direction = 2
keep_probability = 0.75

In [ ]:
def get_supervised_batches(sentences, batch_size):
    """Batch sentences, noisy sentences, and the lengths of their sentences together.
       With each epoch, sentences will receive new mistakes"""
    
    for batch_i in range(0, len(sentences)//batch_size):
        start_i = batch_i * batch_size
        sentences_batch = sentences[start_i:start_i + batch_size]
        
        sentences_batch_noisy = []
        for sentence in sentences_batch:
            sentences_batch_noisy.append(sentence[0])
            
        sentences_batch_eos = []
        for sentence in sentences_batch:
            sent = sentence[1]
            sent.append(vocab_to_int['<EOS>'])
            sentences_batch_eos.append(sent)
            
        pad_sentences_batch = np.array(pad_sentence_batch(sentences_batch_eos))
        pad_sentences_noisy_batch = np.array(pad_sentence_batch(sentences_batch_noisy))
        
        # Need the lengths for the _lengths parameters
        pad_sentences_lengths = []
        for sentence in pad_sentences_batch:
            pad_sentences_lengths.append(len(sentence))
        
        pad_sentences_noisy_lengths = []
        for sentence in pad_sentences_noisy_batch:
            pad_sentences_noisy_lengths.append(len(sentence))
        
        yield pad_sentences_noisy_batch, pad_sentences_batch, pad_sentences_noisy_lengths, pad_sentences_lengths

In [ ]:
def get_unsupervised_batches(sentences, batch_size):
  for batch_i in range(0, len(sentences)//batch_size):
    start_i = batch_i * batch_size
    sentences_batch = np.array(pad_sentence_batch(sentences[start_i:start_i+batch_size]))

    input_lengths = [len(i) for i in sentences_batch]

    yield sentences_batch, input_lengths

In [ ]:
def ids2char(sent):
  return ' '.join([int_to_vocab[i] for i in sent])

In [ ]:
def train_supervised(model, sess_file, epochs, log_string, stop=3):
      '''Train the RNN'''
      saver = tf.train.Saver()
      with tf.Session() as sess:
        
        sess.run(tf.global_variables_initializer())
        #saver.restore(sess, sess_file)

        # Used to determine when to stop the training early
        testing_loss_summary = []

        # Keep track of which batch iteration is being trained
        iteration = 0
        
        display_step = 30 # The progress of the training will be displayed after every 30 batches
        stop_early = 0 
        stop = stop # If the batch_loss_testing does not decrease in k consecutive checks, stop training
        n_batches = int(len(training)/batch_size)
        n_batches_test = int(len(validation)/batch_size)
        testing_check = n_batches

        print()
        print("Training Model: {}".format(log_string))

        train_writer = tf.summary.FileWriter('./logs/1/train/{}'.format(log_string), sess.graph)
        test_writer = tf.summary.FileWriter('./logs/1/test/{}'.format(log_string))

        for epoch_i in range(1, epochs+1):
            batch_loss = 0
            batch_time = 0

            iterator = get_supervised_batches(training, batch_size)

            # For process indication purposes
            iterator = tqdm_notebook(iterator, total=n_batches, desc=f'Epoch {epoch_i}/{epochs}', leave=True)

            # Main training process
            for batch_i, (input_batch, target_batch, input_length, target_length) in enumerate(iterator):
                batch_i += 1

                summary, loss, _ = sess.run([model.merged,
                                              model.cost, 
                                              model.train_op], 
                                              {model.inputs: input_batch,
                                              model.targets: target_batch,
                                              model.inputs_length: input_length,
                                              model.targets_length: target_length,
                                              model.keep_prob: keep_probability})


                batch_loss += loss

                # Record the progress of training
                train_writer.add_summary(summary, iteration)

                iteration += 1

                if batch_i % display_step == 0 and batch_i > 0:
                    iterator.set_postfix(Batch='{:>4}/{}'.format(batch_i, n_batches),
                                        Loss = '{:>6.3f}'.format(batch_loss / display_step))
                    batch_loss = 0
                    batch_time = 0

            #### Validation ####
            batch_loss_testing = 0
            batch_time_testing = 0
            iterator = get_supervised_batches(validation, batch_size)
            iterator = tqdm_notebook(iterator, total = n_batches_test, desc="Testing", leave=True)
            for batch_i, (input_batch, target_batch, input_length, target_length) in enumerate(iterator):
                #start_time_testing = time.time()
                summary, loss = sess.run([model.merged,
                                          model.cost], 
                                              {model.inputs: input_batch,
                                              model.targets: target_batch,
                                              model.inputs_length: input_length,
                                              model.targets_length: target_length,
                                              model.keep_prob: 1})

                batch_loss_testing += loss

                # Record the progress of testing
                test_writer.add_summary(summary, iteration)
          

            n_batches_testing = batch_i + 1
            print('Validation Loss = {:>6.3f}'.format(batch_loss_testing/n_batches_testing))
            testing_loss_summary.append(batch_loss_testing)
            if batch_loss_testing <= min(testing_loss_summary):
                stop_early = 0
                checkpoint = "./{}.ckpt".format(log_string)
                print("New Record!")
                print("Saving ...")
                print("Saved successfully.")
                saver.save(sess, checkpoint)

            else:
                print("No Improvement.")
                stop_early += 1
                if stop_early == stop:
                    break

In [ ]:
def calculate_accuracy(sent_pred, sent_true):
  acc = 0
  seq_len = 0
  for token_pred, token_true in zip(sent_pred, sent_true):
    if token_pred == token_true and int_to_vocab[token_true] not in ('<PAD>','<EOS>'):
      acc += 1
    seq_len += 1
  return acc/seq_len

In [ ]:
def predict_supervised(model, sess_file, sentences, batch_size, map_ids=True):
  '''
  Функция для проверки работы модели на датасете автора оригинальной статьи

  model - тензорфлоуский граф вычислений,
  sess_file - файл, в который мы сохраняли переменные сессии, в том числе веса модели
  sentences - list предложений, которые мы сначала испортим noise maker'ом, а потом восстановим моделью
  '''
  saver = tf.train.Saver()

  acc = []

  with tf.Session() as sess:
    saver.restore(sess, sess_file)
    n_batches = int(len(sentences)//batch_size)
    triplets = []
    iterator = enumerate(get_supervised_batches(sentences, batch_size))
    for batch_i, (input_batch, target_batch, input_length, target_length) in tqdm_notebook(iterator, total=n_batches, leave=True):
    #for batch_i, (input_batch, target_batch, input_length, target_length) in iterator:
                start_time_testing = time.time()
                predictions = sess.run([model.predictions], 
                                        {model.inputs: input_batch,
                                        model.inputs_length: input_length,
                                        model.targets_length: target_length,
                                        model.keep_prob: 1})
                for sent_err, sent_true, sent_pred in zip(input_batch, target_batch, predictions[0]):
                  if map_ids:
                    triplets.append((ids2char(sent_err), ids2char(sent_true), ids2char(sent_pred)))
                  else:
                    triplets.append((sent_err, sent_true, sent_pred))
                  
                  acc.append(calculate_accuracy(sent_pred, sent_true))
  acc = np.mean(acc)
  return triplets, acc

In [ ]:
def predict_unsupervised(model, sess_file, sentences, batch_size, map_ids=True):
  saver = tf.train.Saver()
  with tf.Session() as sess:
    saver.restore(sess, sess_file)
    n_batches = int(len(sentences)//batch_size)
    triplets = []
    iterator = enumerate(get_unsupervised_batches(sentences, batch_size))
    predicted = []
    for batch_i, (input_batch, input_length) in tqdm_notebook(iterator, total=n_batches, leave=True):
    #for batch_i, (input_batch, target_batch, input_length, target_length) in iterator:
                start_time_testing = time.time()
                predictions = sess.run([model.predictions], 
                                        {model.inputs: input_batch,
                                        model.inputs_length: input_length,
                                        model.targets_length: input_length,
                                        model.keep_prob: 1})
                for prediction in predictions[0]:
                  if map_ids:
                    predicted.append(ids2char(prediction))
                  else:
                    predicted.append(prediction)
  return predicted

In [ ]:
# Train the model with the desired tuning parameters
for keep_probability in [0.75]:
    for num_layers in [2]:
        for threshold in [0.95]:
            log_string = 'kp={},nl={},th={}'.format(keep_probability,
                                                    num_layers,
                                                    threshold) 
            model = build_graph(keep_probability, rnn_size, num_layers, batch_size, 
                                learning_rate, embedding_size, direction,
                                vocab_to_int=vocab_to_int)
            train_supervised(model, 'checkpoint.ckpt', 200, log_string, stop=20)

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.

Instructions for updating:
This class is equivalent as tf.keras.layers.LSTMCell, and will be replaced by that in Tensorflow 2.0.
Instructions for updating:
Please use `keras.layers.Bidirectional(keras.layers.RNN(cell))`, which is equivalent to this API
Instructions for updating:
Please use `keras.layers.RNN(cell)`, which is equivalent to this API
Instructions for updating:
Please use `layer.add_weight` method instead.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where

T

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:35: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:68: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`



Validation Loss =  6.404
New Record!
Saving ...
Saved successfully.



Validation Loss =  5.713
New Record!
Saving ...
Saved successfully.


...


Validation Loss =  0.447
No Improvement.



Validation Loss =  0.423
New Record!
Saving ...
Saved successfully.



Validation Loss =  0.434
No Improvement.



Validation Loss =  0.423
New Record!
Saving ...
Saved successfully.



Validation Loss =  0.436
No Improvement.


In [ ]:
train_supervised(model, 'checkpoint.ckpt', 100, log_string, stop=20)


Training Model: kp=0.75,nl=2,th=0.95


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:35: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:68: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`



Validation Loss =  0.948
New Record!
Saving ...
Saved successfully.



Validation Loss =  0.705
New Record!
Saving ...
Saved successfully.


...


Validation Loss =  0.282
New Record!
Saving ...
Saved successfully.



Validation Loss =  0.306
No Improvement.



Validation Loss =  0.285
No Improvement.



Validation Loss =  0.282
No Improvement.



Validation Loss =  0.281
New Record!
Saving ...
Saved successfully.


In [ ]:
os.listdir()

['logs',
 'NewsPunchlinesLateNight.csv',
 'MinEditedHeadlines.csv',
 'Basic seq2seq.ipynb"',
 'kp=0.75,nl=2,th=0.95.ckpt.index',
 'checkpoint',
 'kp=0.75,nl=2,th=0.95.ckpt.data-00000-of-00001',
 'kp=0.75,nl=2,th=0.95.ckpt.meta',
 'Predicted_fun.csv',
 'Predicted_fun_3Datasets.xlsx']

Теперь проверим модель на тестовой выборке

In [ ]:
model = build_graph(keep_probability, rnn_size, num_layers, batch_size, 
                                learning_rate, embedding_size, direction,
                                vocab_to_int=vocab_to_int)

test_triplets, test_acc = predict_supervised(model,'kp=0.75,nl=2,th=0.95.ckpt', testing, batch_size)
train_triplets, train_acc = predict_supervised(model,'kp=0.75,nl=2,th=0.95.ckpt', training, batch_size)

INFO:tensorflow:Restoring parameters from kp=0.75,nl=2,th=0.95.ckpt


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:18: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`



INFO:tensorflow:Restoring parameters from kp=0.75,nl=2,th=0.95.ckpt


In [ ]:
test_acc

0.1039112580128205

In [ ]:
train_acc

0.5531352727620902

In [ ]:
len(train_triplets)

2816

In [ ]:
len(training)

2876

In [ ]:
len(testing)

757

In [ ]:
len(test_triplets)

640

In [ ]:
def clear(s):
  return s[:s.find('<EOS>')]

In [ ]:
test_triplets = [(clear(a),clear(b),clear(c)) for a,b,c in test_triplets]
train_triplets = [(clear(a),clear(b),clear(c)) for a,b,c in train_triplets]

In [ ]:
test_triplets_df = pd.DataFrame(test_triplets, columns=['Serious','Fun','Fun (Predicted)'])
train_triplets_df = pd.DataFrame(train_triplets, columns=['Serious','Fun','Fun (Predicted)'])

In [ ]:
test_triplets_df['Subset'] = 'Test'
train_triplets_df['Subset'] = 'Train'

triplets_df = pd.concat([test_triplets_df,train_triplets_df], ignore_index=True)

In [ ]:
triplets_df.to_excel('Predicted_fun_3Datasets.xlsx')

In [ ]:
os.listdir()

['logs',
 'NewsPunchlinesLateNight.csv',
 'Basic seq2seq.ipynb"',
 'Predicted_fun.csv',
 'MinEditedHeadlines.csv',
 'kp=0.75,nl=2,th=0.95.ckpt.index',
 'checkpoint',
 'kp=0.75,nl=2,th=0.95.ckpt.data-00000-of-00001',
 'kp=0.75,nl=2,th=0.95.ckpt.meta',
 'Predicted_fun_3Datasets.xlsx',
 'unsupervised_news.csv']

In [ ]:
new_headlines = pd.read_csv("unsupervised_news.csv",index_col='Unnamed: 0')

In [ ]:
new_headlines.head()

id  ...   source
0   1  ...  Harvard
1   2  ...  Harvard
2   3  ...  Harvard
3   4  ...  Harvard
4   5  ...  Harvard

[5 rows x 4 columns]

In [ ]:
headlines_sample = new_headlines.sample(n=256)

In [ ]:
def words2id(sent):
  sent = word_tokenize(sent.lower())
  ids = []
  for word in sent:
    if word in vocab_to_int:
      ids.append(vocab_to_int[word])
  return ids

In [ ]:
encoded_headlines = [words2id(sent) for sent in headlines_sample['title']]

In [ ]:
model = build_graph(keep_probability, rnn_size, num_layers, batch_size, 
                                learning_rate, embedding_size, direction,
                                vocab_to_int=vocab_to_int)

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.

Instructions for updating:
This class is equivalent as tf.keras.layers.LSTMCell, and will be replaced by that in Tensorflow 2.0.
Instructions for updating:
Please use `keras.layers.Bidirectional(keras.layers.RNN(cell))`, which is equivalent to this API
Instructions for updating:
Please use `keras.layers.RNN(cell)`, which is equivalent to this API
Instructions for updating:
Please use `layer.add_weight` method instead.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


In [ ]:
predicted_funny_headlines = predict_unsupervised(model, 'kp=0.75,nl=2,th=0.95.ckpt', encoded_headlines, batch_size)

INFO:tensorflow:Restoring parameters from kp=0.75,nl=2,th=0.95.ckpt


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:9: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  if __name__ == '__main__':


In [ ]:
predicted_funny_headlines = [i[:i.find('<EOS>')] for i in predicted_funny_headlines]

In [ ]:
predicted_funny_headlines[:5]

['new skin to inspire new rush onto iraq in iraq skid college life in college ',
 'more than more more more more than more about more about more about more ',
 'flynn : trump called to leaks war with leaks war ',
 "romney 's romney successfully having jacket on use on put on run on run ",
 'legal doctor , legal legal legal in legal , state , government ']

In [ ]:
headlines_sample['predicted fun'] = predicted_funny_headlines

In [ ]:
headlines_sample.head()

id  ...                                      predicted fun
67767    61888  ...  new skin to inspire new rush onto iraq in iraq...
115300  125307  ...  more than more more more more than more about ...
41854    35790  ...  flynn : trump called to leaks war with leaks war 
126654  139198  ...  romney 's romney successfully having jacket on...
350094  203877  ...  legal doctor , legal legal legal in legal , st...

[5 rows x 5 columns]

In [ ]:
headlines_sample.to_excel('Predicted fun news.xlsx')